In [1]:
import django
import os
import pandas as pd
import numpy as np
import html
import namedentities as ne
from old_database.modules_webpage import read_publications, read_addresses, read_seminars

os.environ.setdefault("DJANGO_SETTINGS_MODULE", "nanotud.settings")
from django.core.wsgi import get_wsgi_application
application = get_wsgi_application()
from research.models import Publication


from home.models import Room, Country, Title_full, Gender, Status
from internal.models import Member

from teaching.models import Seminar

# needed when run inter jupyter enviornment:
os.environ["DJANGO_ALLOW_ASYNC_UNSAFE"] = "true"
django.setup()

import gender_guesser.detector as gender
d_gen = gender.Detector()
import re
def define_gender(name):
    male_names=['Jörg','Joerg','Juergen','Jürgen','J&#252;&#776;rgen','Ruediger','Rüdiger',
                'Gunar','Bergoi','Dimitriy','Gianaurelio','Júrgen','R̈udiger','Lei','Saicharan',
                'Shavkat','Faxing','Renhao','Pedram','Xinliang']
    female_names=['Arezoo','Corrina']
    if re.split(' |-',name)[0] in male_names:
        return 'male'
    elif re.split(' |-',name)[0] in female_names:
        return 'female'
    else:
        return d_gen.get_gender(re.split(' |-',name)[0])

Error occurred during loading data. Trying to use cache server https://fake-useragent.herokuapp.com/browsers/0.1.11
Traceback (most recent call last):
  File "/Users/robertb/opt/anaconda3/lib/python3.8/site-packages/fake_useragent/utils.py", line 154, in load
    for item in get_browsers(verify_ssl=verify_ssl):
  File "/Users/robertb/opt/anaconda3/lib/python3.8/site-packages/fake_useragent/utils.py", line 99, in get_browsers
    html = html.split('<table class="w3-table-all notranslate">')[1]
IndexError: list index out of range


FileNotFoundError: [Errno 2] No such file or directory: '/etc/config.json'

## Write old papers database

In [ ]:
path_papers = 'old_database/database.papers'
df_papers = read_publications(path_papers)

# take only publications with DOI
df_papers = df_papers[~df_papers['DOI'].isnull()]

# only publications with reference
df_papers = df_papers[~df_papers['reference'].isnull()]
# df_papers = df_papers[~(df_papers['type']=='inbook')]

In [ ]:
df_papers.columns

**Write to Django Database**

In [ ]:
for index, row in df_papers.iterrows():
    ref=row['reference']
    try:
        journal_short = ref.split('<i>')[1].strip().split('</i>')[0].strip()
    except:
        journal_short = None
        print (ref)
    try:
        volume = ref.split('<b>')[1].split('</b>')[0]
    except:
        volume = None
    try:
        page = ref.split('</b>')[1].split('(')[0].strip(',').strip()
    except:
        page = None
        
    if type(row['pubdate']) == float:
        pubdate = f"{row['year']}-12-01"
    else:
        pubdate = row['pubdate'].replace('.','-')
    try:
        if row['cvselected'] == 'yes': 
            cvselected = 'True'
        else:
            cvselected = 'False'
    except:
        cvselected = 'False'
        
    title = html.unescape(row['title'])
    author_list = html.unescape(row['authors'])
    try:
        abstract = html.unescape(row['abstract'])
    except:
        abstract = None
    if type(row['cover']) == float:
        cover = None
    else:
        cover = 'uploads/publication/img/' + row['cover'].split('/')[-1]

    new_publication = Publication(doi=row['DOI'],
                          page=page,
                          pub_type=row['type'],
                          journal_short=journal_short,
                          cvselected=cvselected,
                          title=title,
                          author_list=author_list,
                          abstract=abstract,
                          volume=volume,
                          year=int(row['year']),
                          pub_date=pubdate,
                                  cover_image=cover
                        )
    
    new_publication.save()

Old stuff:

In [ ]:
len(df_papers['DOI'].unique())

In [ ]:
df_papers[df_papers.duplicated(subset='DOI', keep=False)][['title','DOI','year','cvselected','type']]

In [ ]:
df_papers['type'].unique()

In [ ]:
for col in df_papers.isna().sum().sort_values().index.values:
    try:
        print (col,'\t\tNaN_count:',df_papers[col].isnull().value_counts()[1])
    except:
        print (col,'ALL')

In [ ]:
df_papers[df_papers['reference'].isnull()][['title','DOI','year']]

## Patents and Thesis

## Nanoseminars

In [2]:
path_seminars = 'old_database/database.seminars_22_07_2021'
df_seminars = read_seminars(path_seminars) 

In [ ]:
df_seminars.columns

In [ ]:
df_seminars[df_seminars['room'].isna()]

In [4]:
url=None
for index, row in df_seminars.iterrows():
    date = f"{row['year']}-{row['month']}-{row['day']}"
    title =  html.unescape(row['title'])
    if type(row['affiliation']) != float:
        affil =  html.unescape(row['affiliation'])
    else:
        affil = None
    if type(row['room']) != float:
        room = html.unescape(row['room'])
    else:
        room = None
        if room == 'Zoom meeting':
            url = 'https://tinyurl.com/nanoSeminar-GA'
        else:
            url = None
    if type(row['hour']) != float:
        hour = row['hour'].strip().split(' ')[0].replace('<b>','').replace('</b>','')
    else:
        hour = '10:00'
    date = date + f' {hour}:00'
#     print (html.unescape(row['speaker']))
    room = None
    
    if type(row['talkabstract']) != float:
        abstract = html.unescape(row['talkabstract']).rsplit('<br>  <br> <h3>')[0].rsplit('<br><br> <h3>')[0].rsplit('<br> <h3><a')[0].rsplit('<br>20<a')[0].rsplit('<br><br>  <h3><a')[0]
    else:
        abstract = None
        
    if type(row['announcementpdf']) != float:
        announcement = row['announcementpdf']
#         print (announcement)
    else:
        announcement = None
        
    if type(row['semimage']) != float:
        if row['semimage'].strip() =='':
            image= None
        else:
            image = 'uploads/members/img/' + row['semimage'].strip() + '.jpg'
    
    else:
        image = None
    if type(row['sliderefpdf']) != float:

        slides= row['sliderefpdf'].split('/')[-1]
        if slides.strip() == '':
            slides = None
        else:
            slides = 'uploads/teaching/seminar/' + slides
            print (slides)
    else:
        slides = None
    speaker = html.unescape(row['speaker'])
    new_seminar = Seminar(start_time=date, title=title, abstract=abstract,
                          speaker_name=speaker, speaker_affiliation=affil,
                          image=image, slides=slides, video_conf=url
                        )
    
    new_seminar.save()
        
    

/Users/robertb/opt/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Seminar.start_time received a naive datetime (2021-07-15 13:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"
/Users/robertb/opt/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Seminar.start_time received a naive datetime (2021-07-08 13:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"
/Users/robertb/opt/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Seminar.start_time received a naive datetime (2021-07-01 13:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"
/Users/robertb/opt/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWar

uploads/teaching/seminar/2013_12_19_Oughaddou.pdf


/Users/robertb/opt/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Seminar.start_time received a naive datetime (2013-12-19 13:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"
/Users/robertb/opt/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Seminar.start_time received a naive datetime (2013-12-13 11:10:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"
/Users/robertb/opt/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Seminar.start_time received a naive datetime (2013-12-11 16:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"
/Users/robertb/opt/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWar

uploads/teaching/seminar/2013_10_17_Ingebrandt.pdf


/Users/robertb/opt/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Seminar.start_time received a naive datetime (2013-10-17 13:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"
/Users/robertb/opt/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Seminar.start_time received a naive datetime (2013-09-26 13:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"
/Users/robertb/opt/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Seminar.start_time received a naive datetime (2013-09-19 13:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"


...

/Users/robertb/opt/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Seminar.start_time received a naive datetime (2003-12-08 14:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"
/Users/robertb/opt/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Seminar.start_time received a naive datetime (2003-11-25 15:15:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"


uploads/teaching/seminar/2003_11_19_rafael_gutierrez.pdf


/Users/robertb/opt/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Seminar.start_time received a naive datetime (2003-11-19 10:15:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"
/Users/robertb/opt/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Seminar.start_time received a naive datetime (2003-11-17 16:15:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"


uploads/teaching/seminar/2003_11_14_agapi_emmanouilidou.pdf


/Users/robertb/opt/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Seminar.start_time received a naive datetime (2003-11-14 11:15:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"
/Users/robertb/opt/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Seminar.start_time received a naive datetime (2003-11-03 16:15:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"
/Users/robertb/opt/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWarning: DateTimeField Seminar.start_time received a naive datetime (2003-10-29 14:00:00) while time zone support is active.
  warnings.warn("DateTimeField %s received a naive datetime (%s)"
/Users/robertb/opt/anaconda3/lib/python3.8/site-packages/django/db/models/fields/__init__.py:1416: RuntimeWar

In [ ]:
df_seminars['room'].unique()

## Create Members, Rooms, Academic Titles, Countries

In [ ]:
path_members = 'old_database/database.addresses_chair'
members = read_addresses(path_members)
members.head()

###  Countries

In [ ]:
def set_country(country_old):
    try:
        if country_old in ['Germany','German','Deutsch','Deitsch']:
            return 'German'
        elif country_old in ['Russia','Russian']:
            return'Russia'
        elif country_old in ['Italy','Italian']:
            return 'Italy'
        elif country_old in ['Spain','Spanish']:
            return 'Spain'
        elif country_old in ['Columbia','Colombia']:
            return 'Colombia'
        elif country_old in ['China','Chinese']:
            return 'China'
        elif country_old in ['Greece','Greek']:
            return 'Greece'
        elif country_old in ['India','Indian']:
            return 'India'
        elif country_old in ['Iran','Iranian']:
            return 'Iran'
        elif country_old in ['Mexico','Mexiko']:
            return 'Mexico'
        elif country_old in ['Korea', 'Korean']:
            return 'Korea'
        elif country_old in ['Poland', 'Polish']:
            return 'Poland'
        elif country_old in ['Portugal', 'Portuguese']:
            return 'Portugal'
        elif country_old in ['Turkey', 'Turkish']:
            return 'Turkey'
        
        elif country_old in ['Ukrain', 'Ukraine']:
            return 'Ukraine'
        elif country_old.strip() == '':
            return None
        elif type(country_old) == float:
            return None
        else:
            return country_old
    except:
        print('problems in country', country_old)
        return None
    

In [ ]:
# clean countries:
for index, row in members.iterrows():
    members.loc[index,'nationality'] = set_country(row['nationality'])
members.nationality.unique()

In [ ]:
# # fill country class
# for country in members.nationality.unique():
#     if country != None:
#         new_country = Country(name=country)
#         new_country.save()

### Titles

In [ ]:
def set_title(title_old):
    try:
        if 'DIPL' in title_old.upper():
            return 'Dipl.'
        elif title_old.strip() =='Ms.' or title_old.strip() =='Ms':
            return 'Ms.'
        elif title_old.strip() =='Mr.' or title_old.strip() =='Mr':
            return 'Mr.'
        elif title_old.strip() in ['M. Sc.','MSc.','M.Sc.']:
            return 'M.Sc.'
        elif title_old.strip() in ['B. Sc.','BSc.','B.Sc.']:
            return 'B.Sc.'
        elif title_old.strip()[0:2] == 'Dr' or title_old.strip() in ['PhD']:
            return 'Dr.'
        elif 'Prof' in  title_old.strip():
            return 'Prof.'
        elif 'PD Dr.' == title_old[0:6]:
            return 'PD Dr.'
        elif 'M.A.' == title_old.strip():
            return 'M.A.'
        else:
            print('problems in title', title_old)
            return None
    except:
        return None
    
    return title

def set_last_name(row):
    if type(row['nachname']) != float:
        return html.unescape(row['nachname'])
    else:
        return html.unescape(row['nachnameweb'])

def set_education(education):
    if type(row['education']) == float or row['education'].strip()=='':
        return None
    else:
        return html.unescape(row['education'])

In [ ]:
for index, row in members.iterrows():
    members.loc[index,'titlefull'] = set_title(row['titlefull'])
members.titlefull.unique()

In [ ]:
# for title in members.titlefull.unique():
#     if title != None:
#         new_title = Title_full(title_short=title, title=title)
#         new_title.save()

### Status

In [ ]:
members.status.unique()

In [ ]:
options = ['professor', 'PhD student', 'senior scientist', 'postdoc', 'research assistant', 'secretariat']
# # fill Status class
for status in options:
    new_status = Status(name=status)
    new_status.save()

### Write Members

In [ ]:
members[members['former']!='yes'][['sort_status','nachname']]

In [ ]:
for room in members[members['former'] != 'yes']['room'].unique():
    try:
        id = Room.objects.filter(name__icontains=room.split(' ')[-1])[0].id
        print(room, Room.objects.get(pk=id).name)
    except:
        print(f'room{room} not found')


In [ ]:
options = ['professor', 'PhD', 'senior scientist', 'postdoc', 'research assistant', 'secretariat']
for index, row in members.iterrows():
    
    nachname = set_last_name(row)
    print (nachname)
    vorname = html.unescape(row['vorname'])
    education = set_education(row['education'])
    picture = 'uploads/members/img/' + row['passphoto'].strip() + '.jpg'
    
    member = Member(last_name=nachname, given_name=vorname, education=education, image=picture)
    member.save()
    
    try:
        member.sort_status = row['sort_status'].strip()
    except:
        pass
    try:
        if 'visit' in row['sort_status']:
            member.visitor = True
        else:
            member.visitor = False
    except:
        pass
    
        
    if row['former'] == 'yes':
        member.active = False

        if type(row['formerstartdate']) == float:
            entry_date = f"2010-01-01"
        else:
            entry_date = f"{row['formerstartdate']}-01-01"
        
        exit_date = f"{row['formerenddate']}-12-30"
        member.entry_date = entry_date
        member.exit_date = exit_date
    else:
        member.active = True
        # find room
        try:
            idd = Room.objects.filter(name__icontains=row['room'].split(' ')[-1])[0].id
            room = Room.objects.get(pk=idd)
            member.room.add(room)
        except:
            pass
    

        if (type(row['tel'])==float) or (row['tel'].strip()) == '' or (row['tel']=='Wirtschaftskauffrau') :
            pass
        else:
            member.job_phone = row['tel']
    
    if type(row['briefbio']) == float or row['briefbio'].strip() == '':
        pass
    else:
        member.bio = html.unescape(row['briefbio'])

    
    
    # find country
    try:
        idd = Country.objects.filter(name__icontains=row['nationality'])[0].id
        country = Country.objects.get(pk=idd)
        member.country = country
    except:
        pass
    
    # find title
    try:
        idd = Title_full.objects.filter(title_short__icontains=row['titlefull'])[0].id
        title = Title_full.objects.get(pk=idd)
        member.title = title
    except:
        pass
    
    # Gender
    
    try:
        gender = define_gender(vorname)
        idd = Gender.objects.filter(name__icontains=gender)[0].id
        gender = Gender.objects.get(pk=idd)
        member.gender = gender
        
    except:
        pass
    
    # Status
    try:
        status_db = row['status'].split('(')[0].strip()
        idd = Status.objects.filter(name__icontains=status_db)[0].id
        status = Status.objects.get(pk=idd)
        member.status = status
    except:
        pass
    
    member.save()
    try:
        if type(row['birth_year']) == float or row['birth_year'].strip()=='' or '?' in row['birth_year'] or 'X' in row['birth_year'] or '-' in row['birth_year'] :
            pass
        else:
            member.birth_day = f"{row['birth_year']}-{row['birth_month']}-{row['birth_day']}"
            member.save()
    except:
        pass
    
    